In [79]:
import os 
from tqdm import tqdm 
from copy import deepcopy
import numpy as np
import pandas as pd
from optuna import Trial
from optuna.samplers import TPESampler
import optuna
from sklearn.metrics import f1_score

model_list = os.listdir('predict')

for idx, i in enumerate(model_list):
    globals()['data_{}'.format(idx)] = pd.read_csv(os.path.join('predict', i, 'oof_data.csv'), index_col=0).drop('idx', axis=1).values
    globals()['test_{}'.format(idx)] = pd.read_csv(os.path.join('predict', i, 'checking.csv')).values
    
answer = pd.read_csv('data/train_fold.csv', encoding='cp949')

In [2]:
# 그냥 평균값 구해보면...
length = len(model_list)
pred = None  # (total_len, 4) 

for i in range(length):
    if isinstance(pred, type(None)):
        pred = globals()['data_{}'.format(i)] * (1 / length)
    else:
        pred += globals()['data_{}'.format(i)] * (1 / length)

pred1 = np.argmax(pred[:, :4], axis=1)  # bs, 1
pred2 = np.argmax(pred[:, 4:7], axis=1) # bs, 1
pred3 = np.argmax(pred[:, 7:10], axis=1) # bs, 1
pred4 = np.argmax(pred[:, 10:12], axis=1) # bs, 1


prediction_list = []
for i,j,k,l in zip(pred1, pred2, pred3, pred4):
    prediction_list.append(str(i) + str(j) + str(k) + str(l))
    
ans1 = answer['유형'].to_list()
ans2 = answer['극성'].to_list()
ans3 = answer['시제'].to_list()
ans4 = answer['확실성'].to_list()
    
ans = []
for i,j,k,l in zip(ans1, ans2, ans3, ans4):
    ans.append(str(i) + str(j) + str(k) + str(l))
    
avg_score = f1_score(ans, prediction_list, average='weighted')
print('f1 : ', avg_score)

f1 :  0.7536579446479035


In [73]:
test_0

array([[9.95598440e-01, 4.17963370e-03, 1.11083660e-04, ...,
        1.01999960e-03, 9.98751160e-01, 1.24890220e-03],
       [9.58549000e-01, 4.08444850e-02, 2.47222550e-04, ...,
        1.50892590e-03, 9.92579700e-01, 7.42037100e-03],
       [9.97782230e-01, 1.96698960e-03, 1.04642924e-04, ...,
        7.81798970e-04, 9.94834070e-01, 5.16592500e-03],
       ...,
       [9.95837150e-01, 2.56341980e-03, 1.46921880e-03, ...,
        1.72154770e-01, 9.87674950e-01, 1.23249900e-02],
       [1.27419200e-01, 7.34372260e-01, 4.36348170e-02, ...,
        5.50487940e-01, 8.60135500e-01, 1.39864470e-01],
       [9.53448400e-01, 4.54466640e-02, 4.71947100e-04, ...,
        1.31413900e-04, 9.91480350e-01, 8.51960850e-03]])

-- WEIGHT parametering

In [3]:
length = len(model_list)
# local_data_0 = data_0[:, :4]
# local_data_1 = data_1[:, :4]
# local_data_2 = data_2[:, :4]
# local_data_3 = data_3[:, :4]
# local_data_4 = data_4[:, :4]
# local_data_5 = data_5[:, :4]
# local_data_6 = data_6[:, :4]

def objective(trial):
    
    samples = [1 / length] * length        # [0.15, 0.15, ...]
    
    for i in range(length):
        samples[i] = trial.suggest_uniform('w{}'.format(i), -1, 1)
        
    w = [samples[i] / sum(samples) for i in range(len(samples))]
    
    pred = None  # (total_len, 4) 

    for i in range(length):
        if isinstance(pred, type(None)):
            pred = globals()['data_{}'.format(i)] * w[i]
        else:
            pred += globals()['data_{}'.format(i)] * w[i]
    
    pred1 = np.argmax(pred[:, :4], axis=1)  # bs, 1
    pred2 = np.argmax(pred[:, 4:7], axis=1) # bs, 1
    pred3 = np.argmax(pred[:, 7:10], axis=1) # bs, 1
    pred4 = np.argmax(pred[:, 10:12], axis=1) # bs, 1
    
    prediction_list = []
    for i,j,k,l in zip(pred1, pred2, pred3, pred4):
        prediction_list.append(str(i) + str(j) + str(k) + str(l))
    
    ans1 = answer['유형'].to_list()
    ans2 = answer['극성'].to_list()
    ans3 = answer['시제'].to_list()
    ans4 = answer['확실성'].to_list()
    
    ans = []
    for i,j,k,l in zip(ans1, ans2, ans3, ans4):
        ans.append(str(i) + str(j) + str(k) + str(l))
    
    avg_score = f1_score(ans, prediction_list, average='weighted')

    return avg_score

In [4]:
sampler = TPESampler(seed=42)
study = optuna.create_study(
    study_name="유형",
    direction="maximize",
    sampler=sampler,
)
study.optimize(objective, n_trials=1000)

[I 2022-12-23 00:06:37,030] A new study created in memory with name: 유형
[I 2022-12-23 00:06:37,212] Trial 0 finished with value: 0.7477650896560014 and parameters: {'w0': -0.250919762305275, 'w1': 0.9014286128198323, 'w2': 0.4639878836228102, 'w3': 0.1973169683940732, 'w4': -0.687962719115127, 'w5': -0.6880109593275947, 'w6': -0.8838327756636011, 'w7': 0.7323522915498704, 'w8': 0.2022300234864176, 'w9': 0.416145155592091, 'w10': -0.9588310114083951, 'w11': 0.9398197043239886, 'w12': 0.6648852816008435, 'w13': -0.5753217786434477, 'w14': -0.6363500655857988, 'w15': -0.6331909802931324, 'w16': -0.39151551408092455, 'w17': 0.04951286326447568, 'w18': -0.13610996271576847, 'w19': -0.4175417196039162, 'w20': 0.22370578944475894, 'w21': -0.7210122786959163, 'w22': -0.4157107029295637, 'w23': -0.2672763134126166, 'w24': -0.08786003156592814, 'w25': 0.5703519227860272, 'w26': -0.6006524356832805, 'w27': 0.02846887682722321}. Best is trial 0 with value: 0.7477650896560014.
[I 2022-12-23 00:06:3

[I 2022-12-23 00:06:38,789] Trial 9 finished with value: 0.7537609328278209 and parameters: {'w0': 0.7022733430337138, 'w1': -0.36615598968744467, 'w2': -0.661014506627815, 'w3': 0.11360252491670031, 'w4': 0.8723095483215619, 'w5': 0.392059593349946, 'w6': 0.14012234017872993, 'w7': -0.8056470124584629, 'w8': 0.23001445339833948, 'w9': 0.9801077002085266, 'w10': -0.7198319695269519, 'w11': 0.036659304727473474, 'w12': 0.7547461438559109, 'w13': 0.4815372355084089, 'w14': 0.39403148199053595, 'w15': 0.40496816797421853, 'w16': -0.28101769756048967, 'w17': -0.4128163114710133, 'w18': 0.6187223109570272, 'w19': 0.6202267893583615, 'w20': 0.7341446371602074, 'w21': 0.8264811051129426, 'w22': 0.022684797721875594, 'w23': 0.0030325893743992083, 'w24': 0.5965903579335503, 'w25': 0.2999278615555303, 'w26': 0.4039337545154067, 'w27': 0.5915853388722021}. Best is trial 9 with value: 0.7537609328278209.
[I 2022-12-23 00:06:39,074] Trial 10 finished with value: 0.7532123576617001 and parameters: {

[I 2022-12-23 00:06:42,219] Trial 18 finished with value: 0.7475007860212438 and parameters: {'w0': -0.03599222680892622, 'w1': -0.9464604921476076, 'w2': -0.11779944648287585, 'w3': 0.01766162967126314, 'w4': 0.6325317743137985, 'w5': 0.26342719169197576, 'w6': -0.009806591630877742, 'w7': -0.3608515841803821, 'w8': -0.6719775981962799, 'w9': -0.4509657216628581, 'w10': 0.5070943631911098, 'w11': 0.8031023431561923, 'w12': 0.27088644825617947, 'w13': 0.2461899875742537, 'w14': 0.517038077390251, 'w15': 0.9985130255226081, 'w16': 0.60088683570882, 'w17': -0.24857365977799195, 'w18': 0.6698947013319542, 'w19': 0.29905534412390056, 'w20': -0.19361730924393228, 'w21': 0.31143666385905366, 'w22': -0.9853076474122577, 'w23': -0.9996568719764547, 'w24': 0.20021707081412748, 'w25': 0.9536895486478483, 'w26': 0.2795962604219521, 'w27': 0.2278922751021452}. Best is trial 17 with value: 0.7550875318470318.
[I 2022-12-23 00:06:42,605] Trial 19 finished with value: 0.7504347439542478 and parameter

[I 2022-12-23 00:06:45,744] Trial 27 finished with value: 0.752960293158229 and parameters: {'w0': 0.6366231307306393, 'w1': -0.17679073475002074, 'w2': -0.7329655021685313, 'w3': -0.17238050565990498, 'w4': 0.22240394783323278, 'w5': 0.6639365414100626, 'w6': 0.6844645753168059, 'w7': -0.12964563940593296, 'w8': -0.5266621844627635, 'w9': 0.4638955885524417, 'w10': 0.9930688138536226, 'w11': 0.38402153444066817, 'w12': 0.1229949439692006, 'w13': 0.574889003388103, 'w14': 0.16476729341852495, 'w15': 0.22709884641070716, 'w16': 0.4931116064948547, 'w17': 0.10970955233150725, 'w18': -0.679203513171731, 'w19': 0.15331750931607172, 'w20': 0.5434101726685103, 'w21': 0.10830718998489819, 'w22': 0.29875836244186044, 'w23': 0.016310400522016613, 'w24': 0.15478438278941437, 'w25': 0.8491016868229497, 'w26': 0.4575212790468239, 'w27': 0.5803332260014815}. Best is trial 17 with value: 0.7550875318470318.
[I 2022-12-23 00:06:46,157] Trial 28 finished with value: 0.75396895836638 and parameters: {'

[I 2022-12-23 00:06:49,030] Trial 36 finished with value: 0.608672583188037 and parameters: {'w0': 0.5796873092366364, 'w1': -0.5453621833511697, 'w2': -0.2795582028037023, 'w3': 0.28496436404787506, 'w4': -0.9656976392307758, 'w5': 0.8627274269412073, 'w6': -0.13936738272700605, 'w7': -0.23920948755800706, 'w8': -0.4795315714527684, 'w9': -0.6497239426169905, 'w10': 0.06835415770426759, 'w11': 0.6208515440971824, 'w12': 0.08386741004402778, 'w13': 0.06351484483534053, 'w14': 0.5730340693847101, 'w15': 0.9710962016819225, 'w16': 0.6571747088959657, 'w17': -0.09912483228395008, 'w18': -0.2585374614642493, 'w19': 0.008637777457156565, 'w20': 0.12604732880296998, 'w21': 0.3843729668649561, 'w22': 0.9859831931373236, 'w23': -0.6158485589528333, 'w24': -0.9292335510660932, 'w25': -0.07411951508603529, 'w26': -0.5964584785552869, 'w27': -0.055158931874595835}. Best is trial 17 with value: 0.7550875318470318.
[I 2022-12-23 00:06:49,411] Trial 37 finished with value: 0.7452747040524259 and par

...

[I 2022-12-23 00:14:03,066] Trial 963 finished with value: 0.7580766617098375 and parameters: {'w0': 0.29042939942148027, 'w1': 0.183003252703397, 'w2': 0.43824599178105855, 'w3': -0.07262271704493561, 'w4': 0.15915308432837194, 'w5': 0.6775887348035227, 'w6': -0.5689047067604297, 'w7': -0.5999605437109183, 'w8': -0.32131662113063375, 'w9': 0.055509249132452636, 'w10': 0.027505245733508807, 'w11': -0.1066668539836305, 'w12': 0.1683957847436577, 'w13': 0.8666640737244886, 'w14': 0.7092664407280973, 'w15': 0.387748637322684, 'w16': 0.6102734906926115, 'w17': -0.16772005953641275, 'w18': -0.965643642023354, 'w19': 0.29154922276106143, 'w20': 0.9975728230896486, 'w21': -0.053736445903600466, 'w22': 0.3389132467833892, 'w23': -0.13686241916392852, 'w24': 0.3254767112467102, 'w25': -0.009370310066467056, 'w26': 0.9650165772298179, 'w27': 0.8265989813052546}. Best is trial 747 with value: 0.7591589065046421.
[I 2022-12-23 00:14:03,650] Trial 964 finished with value: 0.7583085005975956 and par

[I 2022-12-23 00:14:08,691] Trial 972 finished with value: 0.7536263743832747 and parameters: {'w0': 0.3796741127046389, 'w1': 0.18055966096536066, 'w2': 0.44502429262617527, 'w3': -0.09291294550447349, 'w4': 0.8787204192558585, 'w5': 0.5816943828788481, 'w6': 0.9325900583741134, 'w7': -0.6794414270657112, 'w8': -0.21341322544710944, 'w9': 0.1338260126520346, 'w10': -0.18197696799628663, 'w11': -0.06661512450171016, 'w12': 0.20913234316177998, 'w13': 0.7509899248227291, 'w14': 0.706485448527371, 'w15': 0.31637233313203256, 'w16': -0.11848649201929358, 'w17': 0.5769152642896299, 'w18': -0.8750451271446064, 'w19': 0.35079034004991705, 'w20': -0.6926575654167817, 'w21': -0.007063427604189598, 'w22': 0.3506564476823412, 'w23': -0.18022240263499012, 'w24': 0.2013317637477183, 'w25': 0.3046789028471568, 'w26': 0.9454110632690786, 'w27': 0.8345380344009682}. Best is trial 747 with value: 0.7591589065046421.
[I 2022-12-23 00:14:09,337] Trial 973 finished with value: 0.7578956140384219 and para

[I 2022-12-23 00:14:14,096] Trial 981 finished with value: 0.7570706813884619 and parameters: {'w0': 0.21417675788140117, 'w1': 0.2224715740885133, 'w2': 0.44900152408773764, 'w3': -0.16133251511791138, 'w4': 0.9982631702832833, 'w5': 0.6081349961708344, 'w6': -0.5964722041290018, 'w7': -0.7043783285843737, 'w8': -0.3496132848502844, 'w9': 0.09832354891672383, 'w10': 0.06354859063870755, 'w11': -0.7987026992468564, 'w12': 0.20516167582868977, 'w13': 0.8913714082797883, 'w14': 0.60241509495037, 'w15': 0.3104775434278136, 'w16': 0.46814041016093544, 'w17': -0.12020825933984763, 'w18': -0.9473363749600936, 'w19': 0.28650422711204776, 'w20': 0.894165361635177, 'w21': -0.02599907373150446, 'w22': 0.37889994222958123, 'w23': -0.19646059553640174, 'w24': 0.3905140015205141, 'w25': 0.06573397998833959, 'w26': 0.904023009390288, 'w27': 0.7801790284308413}. Best is trial 747 with value: 0.7591589065046421.
[I 2022-12-23 00:14:14,639] Trial 982 finished with value: 0.7573221100691546 and paramete

[I 2022-12-23 00:14:19,099] Trial 990 finished with value: 0.7582548176033187 and parameters: {'w0': 0.16251920423452504, 'w1': 0.024421601105102275, 'w2': 0.4707883489653627, 'w3': -0.07504496034561299, 'w4': 0.8806249625978047, 'w5': 0.6237036255153245, 'w6': -0.782723215444108, 'w7': -0.6391428980842994, 'w8': -0.24444922938098662, 'w9': 0.033122514280000535, 'w10': -0.14203977965896225, 'w11': -0.06179930595436313, 'w12': 0.29840448241090495, 'w13': 0.874933690695215, 'w14': 0.5028489428407955, 'w15': 0.3212399572123228, 'w16': 0.5229166950406889, 'w17': -0.16347403605119454, 'w18': -0.875579549969921, 'w19': 0.42642437830537805, 'w20': 0.9618371877638284, 'w21': -0.05133076545051628, 'w22': 0.3273863384490242, 'w23': -0.2584686106266288, 'w24': -0.015164305505244613, 'w25': 0.17210084435650144, 'w26': 0.9990320878458459, 'w27': 0.8568304124679308}. Best is trial 747 with value: 0.7591589065046421.
[I 2022-12-23 00:14:19,628] Trial 991 finished with value: 0.7558474563341222 and pa

[I 2022-12-23 00:14:24,195] Trial 999 finished with value: 0.7536188301638594 and parameters: {'w0': 0.2199075613427274, 'w1': 0.005721343004258597, 'w2': 0.38193976294199306, 'w3': 0.1433651121248205, 'w4': 0.8284645894341821, 'w5': 0.5928412204201041, 'w6': 0.5650985084988819, 'w7': -0.5835353354165224, 'w8': -0.36625619718887475, 'w9': 0.08271293824698525, 'w10': -0.039763269032060844, 'w11': -0.19031588003144637, 'w12': 0.22230635595500714, 'w13': -0.074665387828167, 'w14': 0.6375925071052327, 'w15': -0.18316969120799861, 'w16': 0.45922773530587746, 'w17': -0.1808375495946839, 'w18': -0.9990467064258359, 'w19': 0.23714723518378183, 'w20': 0.9288809857431756, 'w21': 0.1177175504024729, 'w22': 0.5178351765350895, 'w23': -0.13632551092545453, 'w24': 0.5262400468493295, 'w25': 0.03934826983931304, 'w26': 0.8699768505839385, 'w27': 0.6990208821360995}. Best is trial 747 with value: 0.7591589065046421.


In [5]:
print("Best Score:", study.best_value)
print("Best trial:", study.best_trial.params) # 1.9051  0.096 -0.211 0.255 -0.109 0.068 0.4853 0.4146
w = []
for i, j in study.best_trial.params.items():
    w.append(j)
w = [w[i] / sum(w) for i in range(len(w))]
w

Best Score: 0.7591589065046421
Best trial: {'w0': 0.6255878565566564, 'w1': -0.07146322903549529, 'w2': 0.5565010173882302, 'w3': -0.3300434636584283, 'w4': 0.8467523698787665, 'w5': 0.5035751109609045, 'w6': -0.5069841511352107, 'w7': -0.6669250934818616, 'w8': -0.6233686816643362, 'w9': -0.06739607476020351, 'w10': -0.2614223364380285, 'w11': 0.2899407325306155, 'w12': 0.2524489339527634, 'w13': 0.9985953475959494, 'w14': 0.6041466240637569, 'w15': 0.3027676026782591, 'w16': 0.7154240825883925, 'w17': -0.010331833782135938, 'w18': -0.9014941374629488, 'w19': -0.14259750216226597, 'w20': 0.8504778222669388, 'w21': -0.3649446434061675, 'w22': 0.19277876724165421, 'w23': -0.4583019230088587, 'w24': 0.800104312937911, 'w25': 0.7998355248225356, 'w26': 0.5751626033837517, 'w27': 0.8331814895830685}


[0.11710726727165963,
 -0.013377598965586135,
 0.10417451793093083,
 -0.061782670019604934,
 0.15850828153555022,
 0.09426702339659859,
 -0.09490518057092372,
 -0.12484541436344786,
 -0.11669184759157197,
 -0.012616245755545792,
 -0.04893709988639673,
 0.0542756169282012,
 0.04725731880982313,
 0.18693261232855113,
 0.11309356381200436,
 0.056676750030283614,
 0.1339242096440424,
 -0.0019340733798616785,
 -0.1687556972106071,
 -0.02669361884660429,
 0.15920566967049724,
 -0.06831601580305936,
 0.03608732871499542,
 -0.08579208375994639,
 0.14977597253271135,
 0.14972565659173392,
 0.10766788391619699,
 0.15596787303937593]

In [15]:
length = len(model_list)
pred = None  # (total_len, 4) 

for i, j in zip(range(length), w):
    if isinstance(pred, type(None)):
        pred = globals()['test_{}'.format(i)] * j
    else:
        pred += globals()['test_{}'.format(i)] * j
        
y_hats = deepcopy(pred)

pred1 = np.argmax(y_hats[:, :4], axis=1)  # bs, 1
pred2 = np.argmax(y_hats[:, 4:7], axis=1) # bs, 1
pred3 = np.argmax(y_hats[:, 7:10], axis=1) # bs, 1
pred4 = np.argmax(y_hats[:, 10:12], axis=1) # bs, 1
y_df = pd.DataFrame()
y_df['pred1'] = pred1
y_df['pred2'] = pred2
y_df['pred3'] = pred3
y_df['pred4'] = pred4

dict1 = {0: '사실형', 1: '추론형', 2: '예측형', 3: '대화형'}
dict2 = {0: '긍정', 1: '부정', 2: '미정'}
dict3 = {0: '현재', 1: '과거', 2: '미래'}
dict4 = {0: '확실', 1: '불확실'}

y_df['pred1'] = y_df['pred1'].apply(lambda x: dict1[x])
y_df['pred2'] = y_df['pred2'].apply(lambda x: dict2[x])
y_df['pred3'] = y_df['pred3'].apply(lambda x: dict3[x])
y_df['pred4'] = y_df['pred4'].apply(lambda x: dict4[x])

y_df['label'] = y_df['pred1'] + '-' + y_df['pred2'] + '-' + y_df['pred3'] + '-' + y_df['pred4']

submission = pd.read_csv('data/sample_submission.csv', encoding='cp949')

submission['label'] = y_df['label']

submission.to_csv('submission.csv', encoding='utf-8-sig', index=False)

-- apply LGBM

In [42]:
y = pd.get_dummies(data=answer[['유형', '극성', '시제', '확실성']], columns=['유형', '극성', '시제', '확실성'])
from iterstrat.ml_stratifiers import MultilabelStratifiedKFold
Fold = MultilabelStratifiedKFold(n_splits=10)
for n, (train_index, val_index) in enumerate(Fold.split(answer, y)):
    answer.loc[val_index, 'fold2'] = int(n)
answer['fold2'] = answer['fold2'].astype(int)
display(answer.groupby('fold').size())

fold
0    4135
1    4136
2    4135
3    4135
dtype: int64

In [110]:
from lightgbm import LGBMClassifier

In [117]:
data_list = [globals()['data_{}'.format(i)] for i in range(28)]
test_list = [globals()['test_{}'.format(i)] for i in range(28)]


sum_data = pd.DataFrame([])
test_data = pd.DataFrame([])

for idx, data in enumerate(data_list):
    pred = np.argmax(data[:, 10:12], axis=1)  # bs, 1
    sum_data[str(idx)] = pred

for idx, data in enumerate(test_list):
    pred = np.argmax(data[:, 10:12], axis=1)  # bs, 1
    test_data[str(idx)] = pred

    
local = None
for i, j in zip(range(length), w):
    if isinstance(local, type(None)):
        local = globals()['data_{}'.format(i)] * j
    else:
        local += globals()['data_{}'.format(i)] * j
local = np.argmax(local[:, 10:12], axis=1)
sum_data['weight'] = local

local = None
for i, j in zip(range(length), w):
    if isinstance(local, type(None)):
        local = globals()['test_{}'.format(i)] * j
    else:
        local += globals()['test_{}'.format(i)] * j
local = np.argmax(local[:, 10:12], axis=1)
test_data['weight'] = local



k = np.zeros(data_list[0].shape) 
for i in range(len(data_list)):
    k += data_list[i]
k = k / len(data_list)
pred2 = np.argmax(k[:, 10:12], axis=1)  # bs, 1
sum_data['average'] = pred2


k = np.zeros(test_list[0].shape) 
for i in range(len(test_list)):
    k += test_list[i]
k = k / len(test_list)
pred2 = np.argmax(k[:, 10:12], axis=1)  # bs, 1
test_data['average'] = pred2

In [118]:
params_lgb = {
    "random_state": 42,
    "verbosity": -1,
    "learning_rate": 0.08980618671770885,
    "n_estimators": 1000,
    "objective": "binary",
    "metric": "binary_logloss",
    "reg_alpha": 0.0381890350793144,
    "reg_lambda": 0.02550799927837808,
    "max_depth": 8,
#                 "num_leaves": trial.suggest_int("num_leaves", 2, 256),
    "colsample_bytree": 0.5033551909164212,
    "subsample": 0.3260839421071682,
    "subsample_freq": 9,
    "min_child_samples": 68,
    "max_bin": 409,
}
model4 = LGBMClassifier(**params_lgb)
model4.fit(sum_data.values, answer['확실성'])
pred4 = model4.predict(test_data.values)

In [102]:
pred1

array([0, 0, 0, ..., 0, 1, 0], dtype=int64)

In [109]:
pred2

array([0, 0, 0, ..., 0, 0, 0], dtype=int64)

In [116]:
pd.Series(pred3).value_counts()

1    3440
0    3014
2     636
dtype: int64

In [122]:
pd.Series(pred4).value_counts()

0    6684
1     406
dtype: int64

In [124]:
final = pd.DataFrame([])
final['pred1'] = pred1
final['pred2'] = pred2
final['pred3'] = pred3
final['pred4'] = pred4
final

pred1  pred2  pred3  pred4
0         0      0      0      0
1         0      0      0      0
2         0      0      1      0
3         0      0      1      0
4         0      0      1      0
...     ...    ...    ...    ...
7085      0      0      0      0
7086      1      0      0      0
7087      0      0      0      0
7088      1      0      2      0
7089      0      0      1      0

[7090 rows x 4 columns]

In [125]:
dict1 = {0: '사실형', 1: '추론형', 2: '예측형', 3: '대화형'}
dict2 = {0: '긍정', 1: '부정', 2: '미정'}
dict3 = {0: '현재', 1: '과거', 2: '미래'}
dict4 = {0: '확실', 1: '불확실'}

final['pred1'] = final['pred1'].apply(lambda x: dict1[x])
final['pred2'] = final['pred2'].apply(lambda x: dict2[x])
final['pred3'] = final['pred3'].apply(lambda x: dict3[x])
final['pred4'] = final['pred4'].apply(lambda x: dict4[x])


In [127]:
final['label'] = final['pred1'] + '-' + final['pred2'] + '-' + final['pred3'] + '-' + final['pred4']

In [129]:
final

pred1 pred2 pred3 pred4         label
0      사실형    긍정    현재    확실  사실형-긍정-현재-확실
1      사실형    긍정    현재    확실  사실형-긍정-현재-확실
2      사실형    긍정    과거    확실  사실형-긍정-과거-확실
3      사실형    긍정    과거    확실  사실형-긍정-과거-확실
4      사실형    긍정    과거    확실  사실형-긍정-과거-확실
...    ...   ...   ...   ...           ...
7085   사실형    긍정    현재    확실  사실형-긍정-현재-확실
7086   추론형    긍정    현재    확실  추론형-긍정-현재-확실
7087   사실형    긍정    현재    확실  사실형-긍정-현재-확실
7088   추론형    긍정    미래    확실  추론형-긍정-미래-확실
7089   사실형    긍정    과거    확실  사실형-긍정-과거-확실

[7090 rows x 5 columns]

In [130]:
submission = pd.read_csv('data/sample_submission.csv', encoding='cp949')

submission['label'] = final['label']

submission.to_csv('submission.csv', encoding='utf-8-sig', index=False)

In [131]:
submission

ID         label
0     TEST_0000  사실형-긍정-현재-확실
1     TEST_0001  사실형-긍정-현재-확실
2     TEST_0002  사실형-긍정-과거-확실
3     TEST_0003  사실형-긍정-과거-확실
4     TEST_0004  사실형-긍정-과거-확실
...         ...           ...
7085  TEST_7085  사실형-긍정-현재-확실
7086  TEST_7086  추론형-긍정-현재-확실
7087  TEST_7087  사실형-긍정-현재-확실
7088  TEST_7088  추론형-긍정-미래-확실
7089  TEST_7089  사실형-긍정-과거-확실

[7090 rows x 2 columns]

In [ ]:
params_lgb = {
    "random_state": 42,
    "verbosity": -1,
    "learning_rate": 0.05359355574108569,
    "n_estimators": 1000,
    "objective": "regression",
    "metric": "softmax",
    "reg_alpha": 8.970454157557011e-06,
    "reg_lambda": 0.058743503288567166,
    "max_depth": 2,
#                 "num_leaves": trial.suggest_int("num_leaves", 2, 256),
    "colsample_bytree": 0.6617584443512109,
    "subsample": 0.8639912622247888,
    "subsample_freq": 7,
    "min_child_samples": 56,
    "max_bin": 240,
}

params_lgb = {
    "random_state": 42,
    "verbosity": -1,
    "learning_rate": 0.08562108923177253,
    "n_estimators": 1000,
    "objective": "regression",
    "metric": "softmax",
    "reg_alpha": 2.6399874377043225e-06,
    "reg_lambda": 0.012603086400975481,
    "max_depth": 4,
#                 "num_leaves": trial.suggest_int("num_leaves", 2, 256),
    "colsample_bytree": 0.7297821636738198,
    "subsample": 0.7563006389699555,
    "subsample_freq": 6,
    "min_child_samples": 56,
    "max_bin": 323,
}
params_lgb = {
    "random_state": 42,
    "verbosity": -1,
    "learning_rate": 0.09978965120452965,
    "n_estimators": 1000,
    "objective": "regression",
    "metric": "softmax",
    "reg_alpha": 1.8351143462687948e-05,
    "reg_lambda": 0.02550799927837808,
    "max_depth": 2,
#                 "num_leaves": trial.suggest_int("num_leaves", 2, 256),
    "colsample_bytree": 0.7213745584212938,
    "subsample": 0.6373274307643308,
    "subsample_freq": 5,
    "min_child_samples": 63,
    "max_bin": 201,
}
params_lgb = {
    "random_state": 42,
    "verbosity": -1,
    "learning_rate": 0.08980618671770885,
    "n_estimators": 1000,
    "objective": "binary",
    "metric": "binary_logloss",
    "reg_alpha": 0.0381890350793144,
    "reg_lambda": 0.02550799927837808,
    "max_depth": 8,
#                 "num_leaves": trial.suggest_int("num_leaves", 2, 256),
    "colsample_bytree": 0.5033551909164212,
    "subsample": 0.3260839421071682,
    "subsample_freq": 9,
    "min_child_samples": 68,
    "max_bin": 409,
}

-- DNN

-- 각 컬럼 별 weight

In [80]:
length = len(model_list)
sum_data = np.zeros((len(data_0), 4))

In [81]:
length = len(model_list)

def objective(trial):
    samples = [1 / length] * length        # [0.15, 0.15, ...]
    
    for i in range(length):
        samples[i] = trial.suggest_uniform('w{}'.format(i), -1, 1)
        
    w = [samples[i] / sum(samples) for i in range(len(samples))]
    
    pred = None  # (total_len, 4) 

    for i in range(length):
        
        local_data = globals()['data_{}'.format(i)]
        if isinstance(pred, type(None)):
            pred = local_data[:, :4] * w[i]
        else:
            pred += local_data[:, :4] * w[i]
            
    pred = np.argmax(pred, axis=1).tolist()  # bs, 1
        
    ans = answer['유형'].to_list()
        
    avg_score = f1_score(ans, pred, average='weighted')

    return avg_score

sampler = TPESampler(seed=42)
study = optuna.create_study(
    study_name="유형",
    direction="maximize",
    sampler=sampler,
)
study.optimize(objective, n_trials=1000)

w1 = []
for i, j in study.best_trial.params.items():
    w1.append(j)
w1 = [w1[i] / sum(w1) for i in range(len(w1))]

for i in range(length):
    local_data = globals()['data_{}'.format(i)]
    sum_data += local_data[:, :4] * w1[i]
    

[I 2022-12-22 22:13:28,800] A new study created in memory with name: 유형
[I 2022-12-22 22:13:28,825] Trial 0 finished with value: 0.8952258055962034 and parameters: {'w0': -0.250919762305275, 'w1': 0.9014286128198323, 'w2': 0.4639878836228102, 'w3': 0.1973169683940732, 'w4': -0.687962719115127, 'w5': -0.6880109593275947, 'w6': -0.8838327756636011, 'w7': 0.7323522915498704, 'w8': 0.2022300234864176, 'w9': 0.416145155592091, 'w10': -0.9588310114083951, 'w11': 0.9398197043239886, 'w12': 0.6648852816008435, 'w13': -0.5753217786434477, 'w14': -0.6363500655857988, 'w15': -0.6331909802931324, 'w16': -0.39151551408092455, 'w17': 0.04951286326447568, 'w18': -0.13610996271576847, 'w19': -0.4175417196039162, 'w20': 0.22370578944475894, 'w21': -0.7210122786959163, 'w22': -0.4157107029295637, 'w23': -0.2672763134126166, 'w24': -0.08786003156592814, 'w25': 0.5703519227860272, 'w26': -0.6006524356832805, 'w27': 0.02846887682722321}. Best is trial 0 with value: 0.8952258055962034.
[I 2022-12-22 22:13:2

[I 2022-12-22 22:13:29,091] Trial 9 finished with value: 0.8983634770974488 and parameters: {'w0': 0.7022733430337138, 'w1': -0.36615598968744467, 'w2': -0.661014506627815, 'w3': 0.11360252491670031, 'w4': 0.8723095483215619, 'w5': 0.392059593349946, 'w6': 0.14012234017872993, 'w7': -0.8056470124584629, 'w8': 0.23001445339833948, 'w9': 0.9801077002085266, 'w10': -0.7198319695269519, 'w11': 0.036659304727473474, 'w12': 0.7547461438559109, 'w13': 0.4815372355084089, 'w14': 0.39403148199053595, 'w15': 0.40496816797421853, 'w16': -0.28101769756048967, 'w17': -0.4128163114710133, 'w18': 0.6187223109570272, 'w19': 0.6202267893583615, 'w20': 0.7341446371602074, 'w21': 0.8264811051129426, 'w22': 0.022684797721875594, 'w23': 0.0030325893743992083, 'w24': 0.5965903579335503, 'w25': 0.2999278615555303, 'w26': 0.4039337545154067, 'w27': 0.5915853388722021}. Best is trial 9 with value: 0.8983634770974488.
[I 2022-12-22 22:13:29,251] Trial 10 finished with value: 0.897571203116199 and parameters: {'

[I 2022-12-22 22:13:30,198] Trial 18 finished with value: 0.8958048159665246 and parameters: {'w0': -0.1836387680166286, 'w1': -0.26300160563299163, 'w2': -0.1121075190394446, 'w3': 0.6535360762672929, 'w4': -0.26913607009196805, 'w5': -0.2215797245651847, 'w6': 0.4224630035821853, 'w7': -0.3643676093549401, 'w8': 0.7396665660758596, 'w9': 0.721249471180824, 'w10': -0.9691178693102076, 'w11': -0.5302661639936028, 'w12': 0.3324934129530541, 'w13': 0.9519126204945016, 'w14': 0.517038077390251, 'w15': -0.3065894594573897, 'w16': -0.7391203312855177, 'w17': -0.28616094069798026, 'w18': 0.9990946672075944, 'w19': 0.6996763523565087, 'w20': -0.19361730924393228, 'w21': 0.6580299586673585, 'w22': 0.06374613602639563, 'w23': -0.9996568719764547, 'w24': 0.5465887560461966, 'w25': 0.9536895486478483, 'w26': 0.3584145144134308, 'w27': 0.2157116063461316}. Best is trial 9 with value: 0.8983634770974488.
[I 2022-12-22 22:13:30,335] Trial 19 finished with value: 0.8722353605706741 and parameters: {'

[I 2022-12-22 22:13:31,596] Trial 27 finished with value: 0.8990507806170104 and parameters: {'w0': 0.9858418292763667, 'w1': 0.5060813905341888, 'w2': -0.427818333299887, 'w3': -0.17238050565990498, 'w4': -0.34618814282951793, 'w5': 0.3690160120135166, 'w6': -0.5080816779026593, 'w7': -0.8151727899547873, 'w8': -0.6085782363000092, 'w9': 0.3450643337673157, 'w10': -0.5033564567122939, 'w11': 0.39403831432605557, 'w12': 0.5649420808254425, 'w13': 0.37301253821400543, 'w14': 0.9650462926011063, 'w15': 0.5694120750496607, 'w16': 0.09212478881125585, 'w17': -0.42929125955361236, 'w18': 0.016652891241956028, 'w19': 0.31769188875310694, 'w20': 0.48276856406410856, 'w21': 0.6710599604253983, 'w22': 0.7479677337031282, 'w23': -0.637051529667704, 'w24': -0.20652917536087684, 'w25': -0.16768454322294984, 'w26': 0.26680174117815353, 'w27': 0.9871257373204734}. Best is trial 21 with value: 0.8990789479676281.
[I 2022-12-22 22:13:31,741] Trial 28 finished with value: 0.8983480795549662 and paramet

[I 2022-12-22 22:13:32,863] Trial 36 finished with value: 0.8630324420391439 and parameters: {'w0': 0.875067398070965, 'w1': 0.6341830535508814, 'w2': 0.07511443284258768, 'w3': -0.8902661679066614, 'w4': -0.5721166594460803, 'w5': -0.09824954678513015, 'w6': 0.995981807058609, 'w7': -0.8694212177402688, 'w8': -0.6041533910663798, 'w9': -0.20077278503678472, 'w10': -0.4977392003207903, 'w11': 0.5456015171310205, 'w12': -0.053634915164954, 'w13': 0.34296394831823707, 'w14': 0.6006652306946568, 'w15': 0.67979247529138, 'w16': -0.36017931295141736, 'w17': -0.652542557941921, 'w18': -0.34262698398965125, 'w19': 0.11414280539076543, 'w20': 0.15781986339781362, 'w21': -0.9050290281679613, 'w22': 0.9859831931373236, 'w23': -0.3448642769341906, 'w24': 0.2572772594236172, 'w25': 0.031379488979278836, 'w26': -0.22028538890062055, 'w27': 0.8538562935249332}. Best is trial 31 with value: 0.8997566613184773.
[I 2022-12-22 22:13:33,007] Trial 37 finished with value: 0.8788809135533743 and parameters

...

[I 2022-12-22 22:17:53,869] Trial 963 finished with value: 0.901025293354316 and parameters: {'w0': 0.05543369674332341, 'w1': -0.8932488626278945, 'w2': -0.36757919655364096, 'w3': 0.6463211627761122, 'w4': -0.21727026320532608, 'w5': -0.22234299003521885, 'w6': -0.9361237253248021, 'w7': 0.2177575197536043, 'w8': -0.6954556704428514, 'w9': 0.1757099651754733, 'w10': -0.5614597842673338, 'w11': 0.4970171102190603, 'w12': 0.756095964251049, 'w13': 0.9223936651989911, 'w14': 0.8753296392207626, 'w15': 0.33709393530089254, 'w16': -0.37383545125752715, 'w17': 0.13173291274522372, 'w18': -0.060402064671226476, 'w19': 0.28858419739473246, 'w20': 0.16961572194777536, 'w21': 0.467778616902763, 'w22': 0.964113605336568, 'w23': -0.49547669781358306, 'w24': 0.5633553376376306, 'w25': 0.844846420960627, 'w26': 0.8664879378797983, 'w27': 0.04394427234069212}. Best is trial 900 with value: 0.9018883464222354.
[I 2022-12-22 22:17:54,280] Trial 964 finished with value: 0.9001217373499677 and paramete

[I 2022-12-22 22:17:57,491] Trial 972 finished with value: 0.9008501032826104 and parameters: {'w0': 0.06687941708975292, 'w1': -0.9596592598891812, 'w2': -0.4009296917185981, 'w3': 0.6325343713701772, 'w4': -0.28361200002904174, 'w5': -0.10594914465553533, 'w6': -0.9544326543750467, 'w7': 0.23357756723631712, 'w8': -0.6920954299884361, 'w9': 0.1508078045176992, 'w10': -0.5473955379942849, 'w11': 0.5423352900576648, 'w12': 0.7690749945491832, 'w13': 0.9554657235423228, 'w14': 0.8562526352343873, 'w15': 0.36577085957692257, 'w16': -0.35179558059300736, 'w17': 0.21036895994622684, 'w18': -0.063511762264939, 'w19': 0.3102507979941086, 'w20': 0.07775667740795524, 'w21': 0.4508250534667563, 'w22': 0.90045312597623, 'w23': -0.45095543424700824, 'w24': 0.5735404916677634, 'w25': 0.8496897328342046, 'w26': 0.9169505645351637, 'w27': 0.12646926693080146}. Best is trial 900 with value: 0.9018883464222354.
[I 2022-12-22 22:17:57,909] Trial 973 finished with value: 0.9011290065096664 and parameter

[I 2022-12-22 22:18:01,471] Trial 981 finished with value: 0.8986487110430259 and parameters: {'w0': 0.05676119351293832, 'w1': -0.89421265880497, 'w2': -0.3795706602903725, 'w3': 0.5513576104698928, 'w4': -0.43255995873758935, 'w5': -0.16242355914101392, 'w6': -0.9992099106285287, 'w7': 0.10959549793154022, 'w8': -0.6661987936645544, 'w9': 0.1460962033597326, 'w10': -0.6288631051560414, 'w11': -0.22036809473568506, 'w12': 0.6529485184509642, 'w13': 0.8674571316562695, 'w14': 0.9151717656349344, 'w15': 0.3752873581468983, 'w16': -0.39902245394238056, 'w17': 0.24284427013745127, 'w18': -0.09101191754745473, 'w19': 0.39228267494773555, 'w20': 0.13288779254462477, 'w21': 0.3828228448885524, 'w22': 0.8593211497250137, 'w23': -0.47225258421447597, 'w24': 0.46102948992810544, 'w25': 0.8220400421334767, 'w26': 0.8668742378443647, 'w27': 0.1646348640542536}. Best is trial 900 with value: 0.9018883464222354.
[I 2022-12-22 22:18:01,853] Trial 982 finished with value: 0.9011108906989975 and param

[I 2022-12-22 22:18:05,405] Trial 990 finished with value: 0.9006275208671858 and parameters: {'w0': 0.06388942302829269, 'w1': -0.8626195349692891, 'w2': -0.4069695897453971, 'w3': 0.5313406271295518, 'w4': -0.4507129961504467, 'w5': -0.09264777432809711, 'w6': -0.9091651245301939, 'w7': 0.04987416265359899, 'w8': -0.7466723115641439, 'w9': 0.12006661800968116, 'w10': -0.6120651288938039, 'w11': 0.43558184456311416, 'w12': 0.7968302075642327, 'w13': 0.9564607922418823, 'w14': 0.9278508598030267, 'w15': 0.3372444705907212, 'w16': -0.2820413718390459, 'w17': 0.21946097879127102, 'w18': -0.006618865671801033, 'w19': 0.39421882493061255, 'w20': 0.11267729260277187, 'w21': 0.5246324807232743, 'w22': 0.8868424486751074, 'w23': -0.41364326852040206, 'w24': 0.41489646171653877, 'w25': 0.8269656441079798, 'w26': 0.8804204517861407, 'w27': 0.12101354989388988}. Best is trial 900 with value: 0.9018883464222354.
[I 2022-12-22 22:18:05,864] Trial 991 finished with value: 0.8989026454692478 and par

[I 2022-12-22 22:18:09,355] Trial 999 finished with value: 0.9007758305279271 and parameters: {'w0': 0.10175527517622653, 'w1': -0.8918619465637765, 'w2': -0.4393028222101431, 'w3': 0.6804789066894257, 'w4': -0.1314410062150373, 'w5': -0.04664621276364954, 'w6': -0.9991183163006816, 'w7': 0.02864989685992833, 'w8': -0.6805888919422319, 'w9': -0.0068326087638586955, 'w10': -0.5469997286558947, 'w11': 0.4527807452743527, 'w12': 0.67902457025291, 'w13': 0.9171624941665232, 'w14': 0.9519660304373163, 'w15': 0.34746339736135046, 'w16': -0.6514124110746705, 'w17': 0.24182862997982552, 'w18': 0.017389689990403162, 'w19': 0.38528952578377934, 'w20': 0.20322184782202207, 'w21': 0.3661744475265705, 'w22': 0.9748624886714232, 'w23': -0.5561164372800959, 'w24': 0.42461896354696965, 'w25': 0.9566035293024445, 'w26': 0.7987489989124285, 'w27': -0.01612160474880081}. Best is trial 900 with value: 0.9018883464222354.


In [82]:
length = len(model_list)

def objective(trial):
    
    samples = [1 / length] * length        # [0.15, 0.15, ...]
    
    for i in range(length):
        samples[i] = trial.suggest_uniform('w{}'.format(i), -1, 1)
        
    w = [samples[i] / sum(samples) for i in range(len(samples))]
    
    pred = None  # (total_len, 4) 

    for i in range(length):
        
        local_data = globals()['data_{}'.format(i)]
        if isinstance(pred, type(None)):
            pred = local_data[:, 4:7] * w[i]
        else:
            pred += local_data[:, 4:7] * w[i]
    
    pred = np.argmax(pred, axis=1).tolist()  # bs, 1
        
    ans = answer['극성'].to_list()
        
    avg_score = f1_score(ans, pred, average='weighted')

    return avg_score

sampler = TPESampler(seed=42)
study = optuna.create_study(
    study_name="극성",
    direction="maximize",
    sampler=sampler,
)
study.optimize(objective, n_trials=1000)

w2 = []
for i, j in study.best_trial.params.items():
    w2.append(j)
w2 = [w2[i] / sum(w2) for i in range(len(w2))]

sum_local = np.zeros((len(data_0), 3))
for i in range(length):
    local_data = globals()['data_{}'.format(i)]
    sum_local += local_data[:, 4:7] * w2[i]
sum_data = np.concatenate([sum_data, sum_local], axis=1)

[I 2022-12-22 22:18:09,390] A new study created in memory with name: 극성
[I 2022-12-22 22:18:09,417] Trial 0 finished with value: 0.972817012477879 and parameters: {'w0': -0.250919762305275, 'w1': 0.9014286128198323, 'w2': 0.4639878836228102, 'w3': 0.1973169683940732, 'w4': -0.687962719115127, 'w5': -0.6880109593275947, 'w6': -0.8838327756636011, 'w7': 0.7323522915498704, 'w8': 0.2022300234864176, 'w9': 0.416145155592091, 'w10': -0.9588310114083951, 'w11': 0.9398197043239886, 'w12': 0.6648852816008435, 'w13': -0.5753217786434477, 'w14': -0.6363500655857988, 'w15': -0.6331909802931324, 'w16': -0.39151551408092455, 'w17': 0.04951286326447568, 'w18': -0.13610996271576847, 'w19': -0.4175417196039162, 'w20': 0.22370578944475894, 'w21': -0.7210122786959163, 'w22': -0.4157107029295637, 'w23': -0.2672763134126166, 'w24': -0.08786003156592814, 'w25': 0.5703519227860272, 'w26': -0.6006524356832805, 'w27': 0.02846887682722321}. Best is trial 0 with value: 0.972817012477879.
[I 2022-12-22 22:18:09,

[I 2022-12-22 22:18:09,649] Trial 9 finished with value: 0.974672672497948 and parameters: {'w0': 0.7022733430337138, 'w1': -0.36615598968744467, 'w2': -0.661014506627815, 'w3': 0.11360252491670031, 'w4': 0.8723095483215619, 'w5': 0.392059593349946, 'w6': 0.14012234017872993, 'w7': -0.8056470124584629, 'w8': 0.23001445339833948, 'w9': 0.9801077002085266, 'w10': -0.7198319695269519, 'w11': 0.036659304727473474, 'w12': 0.7547461438559109, 'w13': 0.4815372355084089, 'w14': 0.39403148199053595, 'w15': 0.40496816797421853, 'w16': -0.28101769756048967, 'w17': -0.4128163114710133, 'w18': 0.6187223109570272, 'w19': 0.6202267893583615, 'w20': 0.7341446371602074, 'w21': 0.8264811051129426, 'w22': 0.022684797721875594, 'w23': 0.0030325893743992083, 'w24': 0.5965903579335503, 'w25': 0.2999278615555303, 'w26': 0.4039337545154067, 'w27': 0.5915853388722021}. Best is trial 9 with value: 0.974672672497948.
[I 2022-12-22 22:18:09,752] Trial 10 finished with value: 0.9745370613271404 and parameters: {'w

[I 2022-12-22 22:18:10,841] Trial 18 finished with value: 0.9736244824539434 and parameters: {'w0': 0.39956972428523724, 'w1': -0.15625477436991686, 'w2': -0.061952607408931326, 'w3': 0.329040872792432, 'w4': -0.2756007090168867, 'w5': -0.20211399978298605, 'w6': 0.4224630035821853, 'w7': -0.7029000073427745, 'w8': -0.045918486989595886, 'w9': 0.7057408926519273, 'w10': -0.242467420021143, 'w11': 0.1648272894164275, 'w12': 0.15037216192148564, 'w13': 0.1828196728450504, 'w14': 0.13902992845885304, 'w15': 0.9952956224856565, 'w16': 0.03862574704705991, 'w17': -0.6806776157455532, 'w18': 0.4728024957255942, 'w19': -0.7516866198441562, 'w20': -0.19361730924393228, 'w21': 0.2847846339486486, 'w22': 0.7310058963297305, 'w23': -0.6151607405408834, 'w24': 0.12936588703199997, 'w25': -0.06168993563312674, 'w26': 0.40549539816639124, 'w27': 0.008627546892551463}. Best is trial 13 with value: 0.9751363399616626.
[I 2022-12-22 22:18:10,992] Trial 19 finished with value: 0.9746491929421967 and par

[I 2022-12-22 22:18:11,925] Trial 27 finished with value: 0.9680767918683095 and parameters: {'w0': 0.9858418292763667, 'w1': -0.005060490068405902, 'w2': -0.845360627678795, 'w3': 0.3876416798255288, 'w4': 0.6669593671461065, 'w5': 0.6378016452712622, 'w6': -0.4893094977588812, 'w7': 0.30263794793528975, 'w8': 0.7652086967369237, 'w9': 0.45486444876906473, 'w10': 0.09253485285670224, 'w11': -0.3839123571662495, 'w12': -0.17715754198398226, 'w13': 0.14389623871063306, 'w14': -0.8527761286254637, 'w15': -0.9873127884147038, 'w16': 0.22705392939019298, 'w17': -0.863115056748585, 'w18': -0.13313799754180838, 'w19': -0.17963589861741003, 'w20': -0.07178909725547367, 'w21': 0.3838852535283097, 'w22': 0.1843938946215081, 'w23': -0.15771418108585553, 'w24': -0.1881788460084749, 'w25': 0.08186589841773881, 'w26': 0.20803373626390642, 'w27': 0.3051482829811208}. Best is trial 13 with value: 0.9751363399616626.
[I 2022-12-22 22:18:12,035] Trial 28 finished with value: 0.9743420930194817 and para

[I 2022-12-22 22:18:13,015] Trial 36 finished with value: 0.9686408238380645 and parameters: {'w0': 0.002636556106230009, 'w1': 0.7125270982482855, 'w2': -0.28162613786586665, 'w3': -0.4282665625283926, 'w4': 0.8343236151774888, 'w5': 0.7514317103554511, 'w6': 0.7174008862395128, 'w7': 0.5114694267023506, 'w8': -0.45508682386196236, 'w9': -0.12260416651637956, 'w10': 0.5242800567055611, 'w11': 0.010879311953613729, 'w12': 0.6706483280180044, 'w13': -0.4544565411599352, 'w14': -0.5580975751214952, 'w15': -0.413609530765213, 'w16': 0.10121085090043172, 'w17': -0.07221901864703117, 'w18': -0.34262698398965125, 'w19': -0.42964787579546404, 'w20': 0.8285000864186828, 'w21': -0.7560786466324043, 'w22': 0.9859831931373236, 'w23': -0.8700276539502432, 'w24': -0.6969970917331625, 'w25': -0.7727748430561621, 'w26': 0.822553286946, 'w27': -0.10309960499651398}. Best is trial 13 with value: 0.9751363399616626.
[I 2022-12-22 22:18:13,187] Trial 37 finished with value: 0.9718033265885859 and paramet

...

[I 2022-12-22 22:22:33,276] Trial 963 finished with value: 0.9760520257804356 and parameters: {'w0': -0.1858082832977295, 'w1': -0.6570356358201715, 'w2': 0.35061467063942753, 'w3': 0.3758211992727253, 'w4': 0.9638792171914758, 'w5': -0.3328365785208275, 'w6': -0.6567273600139262, 'w7': 0.514587307476666, 'w8': 0.19912923714755498, 'w9': -0.40074467591598134, 'w10': 0.7050578633478717, 'w11': -0.5206861258230199, 'w12': -0.5122784931264883, 'w13': -0.4272025709216305, 'w14': 0.0005120742766991787, 'w15': 0.8616678125434636, 'w16': -0.09059285621482106, 'w17': 0.9563112403453924, 'w18': 0.8012189109213971, 'w19': 0.24540122420737703, 'w20': 0.11422412990859343, 'w21': 0.18743424934577446, 'w22': -0.5239902384060912, 'w23': -0.963325298572271, 'w24': 0.447170265867736, 'w25': 0.9676287901460555, 'w26': 0.8652902163019035, 'w27': 0.47612632758679285}. Best is trial 948 with value: 0.9762328785366584.
[I 2022-12-22 22:22:33,666] Trial 964 finished with value: 0.9758414631404697 and paramet

[I 2022-12-22 22:22:37,073] Trial 972 finished with value: 0.9751092897826128 and parameters: {'w0': -0.28885100489890575, 'w1': -0.5879469756518925, 'w2': 0.36439046040444456, 'w3': 0.37798180180653096, 'w4': 0.8968048893723781, 'w5': -0.3546392170167382, 'w6': 0.4607058007750608, 'w7': 0.5401164234069025, 'w8': 0.383093681522916, 'w9': -0.36235336387152256, 'w10': 0.6948787972017711, 'w11': -0.4391597793308293, 'w12': -0.7089879851616614, 'w13': -0.4243335969791994, 'w14': -0.6869672461207795, 'w15': 0.8656623476920481, 'w16': -0.02196577626646322, 'w17': 0.8954883502309297, 'w18': 0.8352775873521123, 'w19': 0.32777034993345655, 'w20': 0.029424611212077127, 'w21': 0.1507232525909535, 'w22': -0.47104850059003106, 'w23': -0.9111250969042878, 'w24': 0.44097309995265727, 'w25': 0.9121916637187218, 'w26': 0.8721762004120334, 'w27': 0.475021541002832}. Best is trial 948 with value: 0.9762328785366584.
[I 2022-12-22 22:22:37,541] Trial 973 finished with value: 0.9678395668325865 and paramet

[I 2022-12-22 22:22:41,006] Trial 981 finished with value: 0.9756764889441047 and parameters: {'w0': -0.16246384893511584, 'w1': -0.666402256119599, 'w2': 0.23652702077569948, 'w3': 0.35089101810194073, 'w4': 0.95998221845091, 'w5': -0.3815550804046796, 'w6': -0.659965966447231, 'w7': 0.5784539790364173, 'w8': 0.297978618980322, 'w9': -0.4022340925303391, 'w10': 0.7264450120308135, 'w11': -0.5445098281587035, 'w12': -0.613634771511927, 'w13': -0.3766780781098629, 'w14': -0.03681470731566558, 'w15': 0.8711342550496101, 'w16': -0.44573704963988836, 'w17': 0.9569985019565219, 'w18': 0.8686560812347461, 'w19': 0.28665022779654636, 'w20': 0.06116880145317968, 'w21': 0.26466480686938604, 'w22': -0.6425266177181972, 'w23': -0.8548749693518909, 'w24': 0.47047307880604683, 'w25': 0.9267244873114053, 'w26': 0.869382821441745, 'w27': 0.4643341363957533}. Best is trial 948 with value: 0.9762328785366584.
[I 2022-12-22 22:22:41,434] Trial 982 finished with value: 0.9756826241000728 and parameters: 

[I 2022-12-22 22:22:44,827] Trial 990 finished with value: 0.9759049325460954 and parameters: {'w0': -0.1900274625682665, 'w1': -0.6880198579604382, 'w2': 0.6279762425910259, 'w3': 0.40650113350684475, 'w4': 0.9607576697312196, 'w5': -0.43792058062878425, 'w6': -0.6566430650150573, 'w7': 0.5772093979931947, 'w8': 0.23388467536073526, 'w9': -0.31415217002223494, 'w10': 0.6491111483244875, 'w11': -0.5321255912515404, 'w12': -0.4826538385311124, 'w13': -0.32499471480048003, 'w14': -0.0060658972186345686, 'w15': 0.7950569535895695, 'w16': -0.03980013873510642, 'w17': 0.7384921096382585, 'w18': 0.9025356984239555, 'w19': 0.2752057425743487, 'w20': 0.08796136347060243, 'w21': 0.12076819992674351, 'w22': -0.4501763585075546, 'w23': -0.8920623798105324, 'w24': 0.48647498564949504, 'w25': 0.9326008448781871, 'w26': 0.8179020064533793, 'w27': 0.44128543420215816}. Best is trial 948 with value: 0.9762328785366584.
[I 2022-12-22 22:22:45,210] Trial 991 finished with value: 0.9754208393711015 and p

[I 2022-12-22 22:22:48,754] Trial 999 finished with value: 0.9752173743900423 and parameters: {'w0': -0.24623932284941946, 'w1': -0.6136727745077079, 'w2': 0.4559483281384902, 'w3': 0.19626039831978082, 'w4': 0.8561154618741202, 'w5': -0.36494263619085654, 'w6': 0.25511298346019373, 'w7': 0.5784185890548282, 'w8': 0.22465084973362323, 'w9': -0.59205751013825, 'w10': 0.771485117454596, 'w11': -0.5967167897143816, 'w12': -0.6479467785475952, 'w13': -0.3838146887438666, 'w14': 0.019100386942072486, 'w15': 0.8803565940212217, 'w16': -0.02505303944081793, 'w17': 0.9516340224417034, 'w18': 0.8285233221131656, 'w19': 0.3557851609897433, 'w20': 0.06389305619523572, 'w21': 0.16115767655037813, 'w22': -0.6383715795791591, 'w23': -0.9190256454177155, 'w24': 0.46875625255434583, 'w25': 0.8930554022731525, 'w26': 0.9882127687719474, 'w27': 0.6050362885164987}. Best is trial 948 with value: 0.9762328785366584.


In [83]:
length = len(model_list)

def objective(trial):
    
    samples = [1 / length] * length        # [0.15, 0.15, ...]
    
    for i in range(length):
        samples[i] = trial.suggest_uniform('w{}'.format(i), -1, 1)
        
    w = [samples[i] / sum(samples) for i in range(len(samples))]
    
    pred = None  # (total_len, 4) 

    for i in range(length):
        
        local_data = globals()['data_{}'.format(i)]
        if isinstance(pred, type(None)):
            pred = local_data[:, 7:10] * w[i]
        else:
            pred += local_data[:, 7:10] * w[i]
    
    pred = np.argmax(pred, axis=1).tolist()  # bs, 1
        
    ans = answer['시제'].to_list()
        
    avg_score = f1_score(ans, pred, average='weighted')

    return avg_score

sampler = TPESampler(seed=42)
study = optuna.create_study(
    study_name="시제",
    direction="maximize",
    sampler=sampler,
)
study.optimize(objective, n_trials=1000)

w3 = []
for i, j in study.best_trial.params.items():
    w3.append(j)
w3 = [w3[i] / sum(w3) for i in range(len(w3))]

sum_local = np.zeros((len(data_0), 3))
for i in range(length):
    local_data = globals()['data_{}'.format(i)]
    sum_local += local_data[:, 7:10] * w3[i]
sum_data = np.concatenate([sum_data, sum_local], axis=1)

[I 2022-12-22 22:22:48,788] A new study created in memory with name: 시제
[I 2022-12-22 22:22:48,820] Trial 0 finished with value: 0.9077933668753738 and parameters: {'w0': -0.250919762305275, 'w1': 0.9014286128198323, 'w2': 0.4639878836228102, 'w3': 0.1973169683940732, 'w4': -0.687962719115127, 'w5': -0.6880109593275947, 'w6': -0.8838327756636011, 'w7': 0.7323522915498704, 'w8': 0.2022300234864176, 'w9': 0.416145155592091, 'w10': -0.9588310114083951, 'w11': 0.9398197043239886, 'w12': 0.6648852816008435, 'w13': -0.5753217786434477, 'w14': -0.6363500655857988, 'w15': -0.6331909802931324, 'w16': -0.39151551408092455, 'w17': 0.04951286326447568, 'w18': -0.13610996271576847, 'w19': -0.4175417196039162, 'w20': 0.22370578944475894, 'w21': -0.7210122786959163, 'w22': -0.4157107029295637, 'w23': -0.2672763134126166, 'w24': -0.08786003156592814, 'w25': 0.5703519227860272, 'w26': -0.6006524356832805, 'w27': 0.02846887682722321}. Best is trial 0 with value: 0.9077933668753738.
[I 2022-12-22 22:22:4

[I 2022-12-22 22:22:49,131] Trial 9 finished with value: 0.9117276859393889 and parameters: {'w0': 0.7022733430337138, 'w1': -0.36615598968744467, 'w2': -0.661014506627815, 'w3': 0.11360252491670031, 'w4': 0.8723095483215619, 'w5': 0.392059593349946, 'w6': 0.14012234017872993, 'w7': -0.8056470124584629, 'w8': 0.23001445339833948, 'w9': 0.9801077002085266, 'w10': -0.7198319695269519, 'w11': 0.036659304727473474, 'w12': 0.7547461438559109, 'w13': 0.4815372355084089, 'w14': 0.39403148199053595, 'w15': 0.40496816797421853, 'w16': -0.28101769756048967, 'w17': -0.4128163114710133, 'w18': 0.6187223109570272, 'w19': 0.6202267893583615, 'w20': 0.7341446371602074, 'w21': 0.8264811051129426, 'w22': 0.022684797721875594, 'w23': 0.0030325893743992083, 'w24': 0.5965903579335503, 'w25': 0.2999278615555303, 'w26': 0.4039337545154067, 'w27': 0.5915853388722021}. Best is trial 9 with value: 0.9117276859393889.
[I 2022-12-22 22:22:49,323] Trial 10 finished with value: 0.9119670906638988 and parameters: {

[I 2022-12-22 22:22:50,420] Trial 18 finished with value: 0.9097662439389016 and parameters: {'w0': 0.6435544694027631, 'w1': -0.18556665806879297, 'w2': -0.1461868713779091, 'w3': 0.7676708894368942, 'w4': 0.1332012543063164, 'w5': -0.19635756029196053, 'w6': -0.19798908686831365, 'w7': 0.25839466241401093, 'w8': 0.5079975977237485, 'w9': 0.259282281077553, 'w10': 0.3758546810937039, 'w11': -0.14990513727063826, 'w12': -0.03378892707110803, 'w13': 0.8579462197254146, 'w14': -0.03149892293490297, 'w15': 0.4279998424569278, 'w16': -0.1716248406558356, 'w17': -0.22049032015428782, 'w18': -0.7402035627623229, 'w19': 0.8290125986059164, 'w20': -0.19361730924393228, 'w21': 0.9967368254822752, 'w22': 0.45281845506572704, 'w23': -0.5517698733121406, 'w24': -0.38368179757331894, 'w25': -0.9918615351621736, 'w26': 0.37773788030853384, 'w27': 0.7511554470450152}. Best is trial 10 with value: 0.9119670906638988.
[I 2022-12-22 22:22:50,578] Trial 19 finished with value: 0.9076025721426693 and para

[I 2022-12-22 22:22:51,681] Trial 27 finished with value: 0.9109563153376857 and parameters: {'w0': 0.5612669897287157, 'w1': 0.27724779392862453, 'w2': -0.06557787309912999, 'w3': 0.6070965219351213, 'w4': -0.0659810721748838, 'w5': 0.4863335487013798, 'w6': 0.031228072971589582, 'w7': -0.8348795862132249, 'w8': 0.9879934253506379, 'w9': 0.6226533057568582, 'w10': 0.2868685680369014, 'w11': -0.6557445593056915, 'w12': 0.33573317745566833, 'w13': 0.16795886488873912, 'w14': 0.531364505021601, 'w15': -0.9873127884147038, 'w16': 0.18123976611983142, 'w17': -0.5554768450171146, 'w18': -0.8320147604222615, 'w19': 0.31184472091933435, 'w20': 0.6069728962045277, 'w21': 0.35309643989949074, 'w22': 0.7115543712965333, 'w23': 0.7137794935960884, 'w24': 0.4577710585604833, 'w25': -0.4759162072009231, 'w26': 0.5487557951362645, 'w27': 0.6942944654317711}. Best is trial 22 with value: 0.9120250187626435.
[I 2022-12-22 22:22:51,842] Trial 28 finished with value: 0.9080872825818805 and parameters: {

[I 2022-12-22 22:22:53,178] Trial 36 finished with value: 0.911301303531269 and parameters: {'w0': 0.5755986649030431, 'w1': -0.31566923072313663, 'w2': -0.5588138955423216, 'w3': 0.2466207160306823, 'w4': 0.5445235204866803, 'w5': -0.13731242896944057, 'w6': 0.995981807058609, 'w7': -0.1544880621733431, 'w8': -0.5988480028928249, 'w9': 0.5765921446683357, 'w10': -0.765530692764997, 'w11': 0.5654201059749435, 'w12': 0.5895010333805878, 'w13': 0.9652818415723661, 'w14': 0.059235039282392155, 'w15': -0.4079831798865474, 'w16': 0.06924660686840423, 'w17': -0.9648505278385714, 'w18': -0.34262698398965125, 'w19': 0.9723602637309785, 'w20': -0.0851358252110217, 'w21': 0.6015383400918015, 'w22': 0.9859831931373236, 'w23': 0.551042214632393, 'w24': 0.09340407102075207, 'w25': 0.6090060846874945, 'w26': 0.9092353353790026, 'w27': 0.7286571951488842}. Best is trial 22 with value: 0.9120250187626435.
[I 2022-12-22 22:22:53,326] Trial 37 finished with value: 0.9102089186638187 and parameters: {'w0

...

[I 2022-12-22 22:27:20,220] Trial 963 finished with value: 0.9120353677895564 and parameters: {'w0': 0.5302778790095185, 'w1': 0.19395377297089678, 'w2': -0.14328121264512744, 'w3': 0.5132335351012401, 'w4': 0.5010704121155011, 'w5': 0.07121468824488555, 'w6': -0.46946638864089485, 'w7': -0.1001707915243655, 'w8': 0.30704002194850505, 'w9': 0.4182804552325473, 'w10': 0.8684125231021201, 'w11': -0.39639377506131257, 'w12': -0.4394131079470391, 'w13': 0.8801975000098756, 'w14': 0.5915120084057887, 'w15': -0.19013157764773275, 'w16': -0.20867110835844188, 'w17': -0.12007414153072776, 'w18': -0.6905108416989556, 'w19': 0.857015171035568, 'w20': 0.8565084758593389, 'w21': 0.8488004809323049, 'w22': -0.6379802455907835, 'w23': -0.2110269995959987, 'w24': 0.9567986911405357, 'w25': 0.9317962506832423, 'w26': 0.7824867279817239, 'w27': 0.8857723297747984}. Best is trial 902 with value: 0.9140044581426062.
[I 2022-12-22 22:27:20,656] Trial 964 finished with value: 0.9138802597313218 and paramet

[I 2022-12-22 22:27:24,264] Trial 972 finished with value: 0.9119423598444769 and parameters: {'w0': 0.5437795048282398, 'w1': 0.21959363299658202, 'w2': -0.17453514188122055, 'w3': 0.49643076769756717, 'w4': 0.5363208313944068, 'w5': 0.09529023296370161, 'w6': -0.5044604090637478, 'w7': -0.10642936736148834, 'w8': 0.34167588186391806, 'w9': -0.8195205179541556, 'w10': 0.9173020503668567, 'w11': -0.5292661605258607, 'w12': -0.31574530679959933, 'w13': 0.9076681199445609, 'w14': 0.6519310389691176, 'w15': -0.2952014756422576, 'w16': -0.3333731928162287, 'w17': -0.13103457316426861, 'w18': -0.7928096813746722, 'w19': -0.6819857012743843, 'w20': 0.9936950171019377, 'w21': 0.8501240608285288, 'w22': -0.6661887048453877, 'w23': -0.17556312227937335, 'w24': 0.917725640532956, 'w25': 0.966378823519177, 'w26': 0.8516694472044064, 'w27': 0.9989202098182134}. Best is trial 902 with value: 0.9140044581426062.
[I 2022-12-22 22:27:24,752] Trial 973 finished with value: 0.9131310851246606 and parame

[I 2022-12-22 22:27:28,241] Trial 981 finished with value: 0.9133947631867996 and parameters: {'w0': 0.39819719762584965, 'w1': 0.24513542331974048, 'w2': -0.15422752420894886, 'w3': 0.5349685828929366, 'w4': 0.5060308527910281, 'w5': 0.12942857955193815, 'w6': -0.4508840508772478, 'w7': -0.125388589412586, 'w8': 0.41993379690416843, 'w9': -0.7819402392768813, 'w10': 0.9515256245349959, 'w11': -0.5135805687931183, 'w12': -0.3468926092175688, 'w13': 0.8480251881577053, 'w14': 0.6019255705928828, 'w15': -0.2616589534026313, 'w16': -0.08262727681170666, 'w17': -0.05465386584025237, 'w18': -0.6350550249723664, 'w19': 0.8804152390440378, 'w20': 0.93132242114909, 'w21': 0.8700021587975227, 'w22': -0.7622930637366522, 'w23': -0.136493508235018, 'w24': 0.9994588700776886, 'w25': 0.9008134646345819, 'w26': 0.8603240726691425, 'w27': 0.9477212689865224}. Best is trial 902 with value: 0.9140044581426062.
[I 2022-12-22 22:27:28,662] Trial 982 finished with value: 0.9135340180040732 and parameters:

[I 2022-12-22 22:27:32,049] Trial 990 finished with value: 0.9130391579946847 and parameters: {'w0': 0.5366626788541479, 'w1': 0.0861622012533342, 'w2': -0.21669121247648565, 'w3': 0.5149605899141902, 'w4': 0.5363094840181556, 'w5': 0.046660061706684186, 'w6': -0.516391962642318, 'w7': -0.10124512276902814, 'w8': 0.3043403118490529, 'w9': -0.8701776864191121, 'w10': 0.9245295844477606, 'w11': -0.4954795661184346, 'w12': -0.21398304213339098, 'w13': 0.8271880286961132, 'w14': 0.6149863410188293, 'w15': -0.24733557884172688, 'w16': -0.21686202363792006, 'w17': 0.017943935543423186, 'w18': -0.7231296403840981, 'w19': 0.8907205741191287, 'w20': 0.8099972057665481, 'w21': 0.8940593049126688, 'w22': -0.8913282031785345, 'w23': -0.11505265689266958, 'w24': 0.928810188904697, 'w25': 0.9107007824919211, 'w26': 0.8706609786832429, 'w27': 0.8809810199452991}. Best is trial 902 with value: 0.9140044581426062.
[I 2022-12-22 22:27:32,532] Trial 991 finished with value: 0.9133490668094423 and paramet

[I 2022-12-22 22:27:35,610] Trial 999 finished with value: 0.9131155001494213 and parameters: {'w0': 0.42326914210172173, 'w1': 0.19599972520097228, 'w2': -0.10827300507423265, 'w3': 0.6268574944219188, 'w4': 0.473736292233967, 'w5': 0.18536290675825018, 'w6': -0.4942499616597564, 'w7': -0.0708983001400832, 'w8': 0.42718599390392875, 'w9': -0.94288411182714, 'w10': 0.9123271928680828, 'w11': -0.4966031549261329, 'w12': -0.2843507820819858, 'w13': 0.7272381104266223, 'w14': 0.6012366326389603, 'w15': 0.0254395832546834, 'w16': -0.43899909055209685, 'w17': 0.18147293331879122, 'w18': -0.6757475414041609, 'w19': 0.8887403594820494, 'w20': 0.9406500997786756, 'w21': 0.8619702752314296, 'w22': -0.6060753495222988, 'w23': -0.1681062530428215, 'w24': 0.9975436584843087, 'w25': 0.9027434621776296, 'w26': 0.7471438525233106, 'w27': 0.8845177659981039}. Best is trial 902 with value: 0.9140044581426062.


In [84]:
length = len(model_list)

def objective(trial):
    
    samples = [1 / length] * length        # [0.15, 0.15, ...]
    
    for i in range(length):
        samples[i] = trial.suggest_uniform('w{}'.format(i), -1, 1)
        
    w = [samples[i] / sum(samples) for i in range(len(samples))]
    
    pred = None  # (total_len, 4) 

    for i in range(length):
        
        local_data = globals()['data_{}'.format(i)]
        if isinstance(pred, type(None)):
            pred = local_data[:, 10:12] * w[i]
        else:
            pred += local_data[:, 10:12] * w[i]
    
    pred = np.argmax(pred, axis=1).tolist()  # bs, 1
        
    ans = answer['확실성'].to_list()
        
    avg_score = f1_score(ans, pred, average='weighted')

    return avg_score

sampler = TPESampler(seed=42)
study = optuna.create_study(
    study_name="확실성",
    direction="maximize",
    sampler=sampler,
)
study.optimize(objective, n_trials=1000)

w4 = []
for i, j in study.best_trial.params.items():
    w4.append(j)
w4 = [w4[i] / sum(w4) for i in range(len(w4))]

sum_local = np.zeros((len(data_0), 2))
for i in range(length):
    local_data = globals()['data_{}'.format(i)]
    sum_local += local_data[:, 10:12] * w4[i]
sum_data = np.concatenate([sum_data, sum_local], axis=1)

[I 2022-12-22 22:27:35,648] A new study created in memory with name: 확실성
[I 2022-12-22 22:27:35,715] Trial 0 finished with value: 0.9312399623576374 and parameters: {'w0': -0.250919762305275, 'w1': 0.9014286128198323, 'w2': 0.4639878836228102, 'w3': 0.1973169683940732, 'w4': -0.687962719115127, 'w5': -0.6880109593275947, 'w6': -0.8838327756636011, 'w7': 0.7323522915498704, 'w8': 0.2022300234864176, 'w9': 0.416145155592091, 'w10': -0.9588310114083951, 'w11': 0.9398197043239886, 'w12': 0.6648852816008435, 'w13': -0.5753217786434477, 'w14': -0.6363500655857988, 'w15': -0.6331909802931324, 'w16': -0.39151551408092455, 'w17': 0.04951286326447568, 'w18': -0.13610996271576847, 'w19': -0.4175417196039162, 'w20': 0.22370578944475894, 'w21': -0.7210122786959163, 'w22': -0.4157107029295637, 'w23': -0.2672763134126166, 'w24': -0.08786003156592814, 'w25': 0.5703519227860272, 'w26': -0.6006524356832805, 'w27': 0.02846887682722321}. Best is trial 0 with value: 0.9312399623576374.
[I 2022-12-22 22:27:

[I 2022-12-22 22:27:35,986] Trial 9 finished with value: 0.9318199400012743 and parameters: {'w0': 0.7022733430337138, 'w1': -0.36615598968744467, 'w2': -0.661014506627815, 'w3': 0.11360252491670031, 'w4': 0.8723095483215619, 'w5': 0.392059593349946, 'w6': 0.14012234017872993, 'w7': -0.8056470124584629, 'w8': 0.23001445339833948, 'w9': 0.9801077002085266, 'w10': -0.7198319695269519, 'w11': 0.036659304727473474, 'w12': 0.7547461438559109, 'w13': 0.4815372355084089, 'w14': 0.39403148199053595, 'w15': 0.40496816797421853, 'w16': -0.28101769756048967, 'w17': -0.4128163114710133, 'w18': 0.6187223109570272, 'w19': 0.6202267893583615, 'w20': 0.7341446371602074, 'w21': 0.8264811051129426, 'w22': 0.022684797721875594, 'w23': 0.0030325893743992083, 'w24': 0.5965903579335503, 'w25': 0.2999278615555303, 'w26': 0.4039337545154067, 'w27': 0.5915853388722021}. Best is trial 9 with value: 0.9318199400012743.
[I 2022-12-22 22:27:36,097] Trial 10 finished with value: 0.9316003544363943 and parameters: {

[I 2022-12-22 22:27:37,176] Trial 18 finished with value: 0.9320514782132715 and parameters: {'w0': -0.11764698328709855, 'w1': -0.7672289203594511, 'w2': -0.21593631134192925, 'w3': -0.36648477213578173, 'w4': -0.6625182996390249, 'w5': 0.06760710088800992, 'w6': 0.981873381092043, 'w7': 0.27029514156854195, 'w8': 0.9218491130479098, 'w9': 0.6630771714916608, 'w10': -0.8039198193465191, 'w11': 0.1637832955873318, 'w12': 0.22062482822295082, 'w13': 0.7640507933536342, 'w14': 0.7661815813069359, 'w15': 0.9757635371105473, 'w16': -0.1809849149507513, 'w17': -0.6503499332356908, 'w18': 0.07061808657487334, 'w19': 0.22982904598584986, 'w20': 0.9770768371555862, 'w21': -0.2435111704141792, 'w22': 0.6123514587561849, 'w23': -0.5355033375740064, 'w24': 0.993195956711426, 'w25': 0.14760942459043375, 'w26': 0.3348541691452843, 'w27': 0.6674557810673232}. Best is trial 18 with value: 0.9320514782132715.
[I 2022-12-22 22:27:37,334] Trial 19 finished with value: 0.9324108996117174 and parameters: 

[I 2022-12-22 22:27:38,351] Trial 27 finished with value: 0.9316554535826728 and parameters: {'w0': -0.29521257609147794, 'w1': -0.6459703736203714, 'w2': -0.3007111405351633, 'w3': 0.6543732752523221, 'w4': -0.8272751193945193, 'w5': 0.27980384846456596, 'w6': 0.7835355939442901, 'w7': 0.6182724373179023, 'w8': 0.3892033251389722, 'w9': 0.5727500756647395, 'w10': 0.9930688138536226, 'w11': -0.45738793731973565, 'w12': 0.6204573292067395, 'w13': -0.3828529523557203, 'w14': 0.9930677647497326, 'w15': 0.23089829875558532, 'w16': 0.5682690577773322, 'w17': -0.11200980975316788, 'w18': -0.8563784054088414, 'w19': -0.34531313658824275, 'w20': 0.3254032857222431, 'w21': -0.12451493681768469, 'w22': 0.4855932745073571, 'w23': 0.03339361093460394, 'w24': 0.7392180180093192, 'w25': -0.6567042394113515, 'w26': 0.7881339136998321, 'w27': 0.8110116443567746}. Best is trial 24 with value: 0.9328047953384153.
[I 2022-12-22 22:27:38,491] Trial 28 finished with value: 0.9316696078381778 and parameters

[I 2022-12-22 22:27:39,724] Trial 36 finished with value: 0.9324574621523585 and parameters: {'w0': -0.31311805187003855, 'w1': -0.58986327956436, 'w2': 0.3848181106377498, 'w3': -0.10476345667888168, 'w4': -0.32320357205111905, 'w5': -0.10959930371761965, 'w6': 0.5828150250333957, 'w7': 0.8265473138138952, 'w8': 0.5721523455704344, 'w9': 0.2328733098833407, 'w10': 0.9455901743795624, 'w11': 0.9947375687550594, 'w12': 0.8311797629256449, 'w13': 0.902170489079104, 'w14': -0.44217675726848116, 'w15': 0.8083354270095732, 'w16': -0.8240523947330536, 'w17': 0.114182408103494, 'w18': -0.41422287421294346, 'w19': 0.008399175959429406, 'w20': 0.19477635893422252, 'w21': 0.3229483480890605, 'w22': 0.21274960616075134, 'w23': 0.6080586022494318, 'w24': 0.6422654085203857, 'w25': -0.42314535033953327, 'w26': -0.17597526232160954, 'w27': 0.883101674993404}. Best is trial 35 with value: 0.9328407589822602.
[I 2022-12-22 22:27:39,869] Trial 37 finished with value: 0.9324313613944115 and parameters: 

...

[I 2022-12-22 22:31:43,562] Trial 963 finished with value: 0.9334628458123717 and parameters: {'w0': 0.835954149289474, 'w1': -0.8061401516009328, 'w2': 0.8752861069874162, 'w3': 0.5283728095299755, 'w4': -0.8204940159542051, 'w5': 0.10779198161902842, 'w6': -0.6023572987493535, 'w7': 0.9250965922225909, 'w8': -0.1610401011433093, 'w9': 0.9314691912751636, 'w10': 0.9085301830316901, 'w11': 0.12305910847399879, 'w12': 0.5264003240536766, 'w13': 0.8953881245326194, 'w14': -0.8357369100918213, 'w15': 0.41428912897650827, 'w16': -0.887877627510892, 'w17': 0.9896176549315371, 'w18': -0.07510473097417533, 'w19': -0.5559766681953856, 'w20': 0.9092407998105153, 'w21': -0.7083038877779367, 'w22': 0.723588337433848, 'w23': -0.999486221496125, 'w24': 0.8416996010292263, 'w25': 0.9086818608423377, 'w26': 0.7461145826837157, 'w27': 0.19245641271268335}. Best is trial 620 with value: 0.9343711309237586.
[I 2022-12-22 22:31:43,990] Trial 964 finished with value: 0.9320958632742038 and parameters: {'w

[I 2022-12-22 22:31:47,292] Trial 972 finished with value: 0.9334522391879836 and parameters: {'w0': 0.9995159285242707, 'w1': -0.7857254180134455, 'w2': 0.6036323811968041, 'w3': 0.832836298758356, 'w4': -0.9998992974410573, 'w5': 0.23014113991694884, 'w6': -0.4459301748385397, 'w7': 0.9028255669073596, 'w8': -0.16636126296873271, 'w9': 0.9612974418039708, 'w10': 0.8949792152202367, 'w11': -0.3350668442042223, 'w12': 0.15706090777390305, 'w13': 0.9672377751977659, 'w14': -0.2950338031260672, 'w15': 0.4183113701934597, 'w16': -0.5664370599503996, 'w17': 0.036048724096505946, 'w18': -0.17648753698921119, 'w19': -0.9288511609684333, 'w20': 0.9640541225830068, 'w21': -0.26589113989501095, 'w22': 0.6539613432060042, 'w23': -0.9138633162929871, 'w24': 0.5755404065603762, 'w25': 0.717170595935381, 'w26': 0.8869652415460497, 'w27': 0.10672376384577141}. Best is trial 620 with value: 0.9343711309237586.
[I 2022-12-22 22:31:47,790] Trial 973 finished with value: 0.9314689008233394 and parameter

[I 2022-12-22 22:31:50,745] Trial 981 finished with value: 0.9326936545029768 and parameters: {'w0': 0.6003751811761818, 'w1': -0.7863073633081838, 'w2': 0.7105673033691962, 'w3': 0.7506468065630023, 'w4': -0.9977853373100852, 'w5': 0.03938323099723204, 'w6': -0.7883953368880532, 'w7': 0.888657479947791, 'w8': -0.26440703590300707, 'w9': 0.9316780384522745, 'w10': 0.24470936149629874, 'w11': -0.3628813347718054, 'w12': 0.6106559957375559, 'w13': 0.839659683791898, 'w14': -0.9048752142875093, 'w15': 0.48037104374906436, 'w16': -0.5851457264818815, 'w17': -0.011130059882961112, 'w18': -0.023748541009884078, 'w19': -0.8487562242899399, 'w20': 0.8768826122680271, 'w21': -0.782616535609453, 'w22': 0.637464850186654, 'w23': -0.9411166582348535, 'w24': 0.5747689858617848, 'w25': 0.666810493736648, 'w26': 0.7928488465513706, 'w27': 0.04870712127429989}. Best is trial 620 with value: 0.9343711309237586.
[I 2022-12-22 22:31:51,116] Trial 982 finished with value: 0.9300631192962956 and parameters

[I 2022-12-22 22:31:54,395] Trial 990 finished with value: 0.9341064513167379 and parameters: {'w0': 0.9134227489311483, 'w1': -0.6500958259525338, 'w2': 0.4115407198027369, 'w3': 0.89660414513264, 'w4': -0.9288181400337244, 'w5': -0.10938439828347488, 'w6': -0.6026485312884444, 'w7': 0.9668481366964853, 'w8': -0.09593168953021021, 'w9': 0.9645880287022739, 'w10': 0.9958648843721283, 'w11': -0.04905012456732237, 'w12': 0.34145981882296894, 'w13': 0.8951470653175254, 'w14': -0.9379517328121956, 'w15': 0.2654280958973099, 'w16': -0.5642140300261671, 'w17': -0.4478254469973144, 'w18': 0.15606758018224637, 'w19': -0.7836327809837385, 'w20': 0.9651930002070391, 'w21': -0.42160756811939626, 'w22': 0.3901000876343811, 'w23': -0.8080764609599566, 'w24': 0.7889462687826113, 'w25': 0.5273610774676495, 'w26': 0.7794537459144497, 'w27': 0.508061459611605}. Best is trial 620 with value: 0.9343711309237586.
[I 2022-12-22 22:31:54,812] Trial 991 finished with value: 0.932811882580328 and parameters: 

[I 2022-12-22 22:31:57,794] Trial 999 finished with value: 0.9323599771720662 and parameters: {'w0': 0.7434014663476111, 'w1': -0.6984552104116075, 'w2': 0.38838310611418225, 'w3': 0.9171752176604464, 'w4': -0.9387640080594098, 'w5': -0.15463330658604077, 'w6': -0.8405375696242514, 'w7': 0.921481349052459, 'w8': -0.12049765565476729, 'w9': -0.999953906428169, 'w10': 0.9652422262829683, 'w11': -0.17058557797313822, 'w12': 0.2656268992150561, 'w13': 0.9182691311138096, 'w14': -0.9180340670945176, 'w15': 0.38805926379615086, 'w16': -0.7219997209812352, 'w17': -0.3348360137999014, 'w18': 0.18629590788139522, 'w19': -0.6225383558044686, 'w20': 0.9329066661683799, 'w21': -0.4496019938591083, 'w22': 0.4657226709789814, 'w23': -0.8646612960337615, 'w24': 0.7094701917665162, 'w25': 0.5826938860532911, 'w26': 0.8216573587392091, 'w27': 0.363964378538586}. Best is trial 620 with value: 0.9343711309237586.


In [86]:
pred1 = np.argmax(sum_data[:, :4], axis=1)  # bs, 1
pred2 = np.argmax(sum_data[:, 4:7], axis=1) # bs, 1
pred3 = np.argmax(sum_data[:, 7:10], axis=1) # bs, 1
pred4 = np.argmax(sum_data[:, 10:12], axis=1) # bs, 1
    
prediction_list = []
for i,j,k,l in zip(pred1, pred2, pred3, pred4):
    prediction_list.append(str(i) + str(j) + str(k) + str(l))
    
ans1 = answer['유형'].to_list()
ans2 = answer['극성'].to_list()
ans3 = answer['시제'].to_list()
ans4 = answer['확실성'].to_list()
    
ans = []
for i,j,k,l in zip(ans1, ans2, ans3, ans4):
    ans.append(str(i) + str(j) + str(k) + str(l))
    
avg_score = f1_score(ans, prediction_list, average='weighted')
print('f1 : ', avg_score)

f1 :  0.7625799424750316


In [95]:
sum_data

array([[ 1.04558726, -0.04558728],
       [ 1.0607194 , -0.06071932],
       [ 1.06006842, -0.06006841],
       ...,
       [ 1.04730818, -0.04730815],
       [ 0.88883114,  0.11116888],
       [ 1.05279728, -0.05279736]])

In [85]:
from copy import deepcopy

In [89]:
len(w2)

28

In [90]:
test_0

array([[9.95598440e-01, 4.17963370e-03, 1.11083660e-04, ...,
        1.01999960e-03, 9.98751160e-01, 1.24890220e-03],
       [9.58549000e-01, 4.08444850e-02, 2.47222550e-04, ...,
        1.50892590e-03, 9.92579700e-01, 7.42037100e-03],
       [9.97782230e-01, 1.96698960e-03, 1.04642924e-04, ...,
        7.81798970e-04, 9.94834070e-01, 5.16592500e-03],
       ...,
       [9.95837150e-01, 2.56341980e-03, 1.46921880e-03, ...,
        1.72154770e-01, 9.87674950e-01, 1.23249900e-02],
       [1.27419200e-01, 7.34372260e-01, 4.36348170e-02, ...,
        5.50487940e-01, 8.60135500e-01, 1.39864470e-01],
       [9.53448400e-01, 4.54466640e-02, 4.71947100e-04, ...,
        1.31413900e-04, 9.91480350e-01, 8.51960850e-03]])

In [91]:
length = len(model_list)

sum_data = np.zeros((len(test_0), 4))
for i, j in zip(range(length), w1):
    local_data = globals()['test_{}'.format(i)]
    sum_data += local_data[:, :4] * j
final = deepcopy(sum_data)

sum_data = np.zeros((len(test_0), 3))
for i, j in zip(range(length), w2):
    local_data = globals()['test_{}'.format(i)]
    sum_data += local_data[:, 4:7] * j
final = np.concatenate((final, sum_data), axis=1)

sum_data = np.zeros((len(test_0), 3))
for i, j in zip(range(length), w3):
    local_data = globals()['test_{}'.format(i)]
    sum_data += local_data[:, 7:10] * j
final = np.concatenate((final, sum_data), axis=1)

sum_data = np.zeros((len(test_0), 2))
for i, j in zip(range(length), w4):
    local_data = globals()['test_{}'.format(i)]
    sum_data += local_data[:, 10:12] * j
final = np.concatenate((final, sum_data), axis=1)



y_hats = deepcopy(final)

pred1 = np.argmax(y_hats[:, :4], axis=1)  # bs, 1
pred2 = np.argmax(y_hats[:, 4:7], axis=1) # bs, 1
pred3 = np.argmax(y_hats[:, 7:10], axis=1) # bs, 1
pred4 = np.argmax(y_hats[:, 10:12], axis=1) # bs, 1
y_df = pd.DataFrame()
y_df['pred1'] = pred1
y_df['pred2'] = pred2
y_df['pred3'] = pred3
y_df['pred4'] = pred4

dict1 = {0: '사실형', 1: '추론형', 2: '예측형', 3: '대화형'}
dict2 = {0: '긍정', 1: '부정', 2: '미정'}
dict3 = {0: '현재', 1: '과거', 2: '미래'}
dict4 = {0: '확실', 1: '불확실'}

y_df['pred1'] = y_df['pred1'].apply(lambda x: dict1[x])
y_df['pred2'] = y_df['pred2'].apply(lambda x: dict2[x])
y_df['pred3'] = y_df['pred3'].apply(lambda x: dict3[x])
y_df['pred4'] = y_df['pred4'].apply(lambda x: dict4[x])

y_df['label'] = y_df['pred1'] + '-' + y_df['pred2'] + '-' + y_df['pred3'] + '-' + y_df['pred4']

submission = pd.read_csv('data/sample_submission.csv', encoding='cp949')

submission['label'] = y_df['label']

submission.to_csv('submission.csv', encoding='utf-8-sig', index=False)

In [103]:
saved = deepcopy(y_hats)

In [107]:
sum_data

array([[ 1.04558726, -0.04558728],
       [ 1.0607194 , -0.06071932],
       [ 1.06006842, -0.06006841],
       ...,
       [ 1.04730818, -0.04730815],
       [ 0.88883114,  0.11116888],
       [ 1.05279728, -0.05279736]])

In [112]:
data = pd.DataFrame([]) # 평균값 사용
data['pred1'] = pred1
data['pred2'] = pred2
data['pred3'] = pred3
data['pred4'] = pred4

In [118]:
dict1 = {0: '사실형', 1: '추론형', 2: '예측형', 3: '대화형'}
dict2 = {0: '긍정', 1: '부정', 2: '미정'}
dict3 = {0: '현재', 1: '과거', 2: '미래'}
dict4 = {0: '확실', 1: '불확실'}

data['pred1'] = data['pred1'].apply(lambda x: dict1[x])
data['pred2'] = data['pred2'].apply(lambda x: dict2[x])
data['pred3'] = data['pred3'].apply(lambda x: dict3[x])
data['pred4'] = data['pred4'].apply(lambda x: dict4[x])

# answer['유형'] = answer['유형'].apply(lambda x: dict1[x])
# answer['극성'] = answer['극성'].apply(lambda x: dict2[x])
# answer['시제'] = answer['시제'].apply(lambda x: dict3[x])
# answer['확실성'] = answer['확실성'].apply(lambda x: dict4[x])

In [124]:
data.columns = ['유형', '극성', '시제', '확실성']

In [122]:
answer

Unnamed: 0           ID  \
0               0  TRAIN_00000   
1               1  TRAIN_00001   
2               2  TRAIN_00002   
3               3  TRAIN_00003   
4               4  TRAIN_00004   
...           ...          ...   
16536       16536  TRAIN_16536   
16537       16537  TRAIN_16537   
16538       16538  TRAIN_16538   
16539       16539  TRAIN_16539   
16540       16540  TRAIN_16540   

                                                      문장   유형  극성  시제  확실성  \
0                  0.75%포인트 금리 인상은 1994년 이후 28년 만에 처음이다.  사실형  긍정  현재   확실   
1      이어 ＂앞으로 전문가들과 함께 4주 단위로 상황을 재평가할 예정＂이라며 ＂그 이전이...  사실형  긍정  과거   확실   
2      정부가 고유가 대응을 위해 7월부터 연말까지 유류세 인하 폭을 30%에서 37%까지...  사실형  긍정  미래   확실   
3      서울시는 올해 3월 즉시 견인 유예시간 60분을 제공하겠다고 밝혔지만, 하루 만에 ...  사실형  긍정  과거   확실   
4               익사한 자는 사다리에 태워 거꾸로 놓고 소금으로 코를 막아 가득 채운다.  사실형  긍정  현재   확실   
...                                                  ...  ...  ..  ..  ...   
16536  ＇신동덤＇은 ＇신비한 동물사전＇과 ＇해리 포터＇ 시리즈를 잇는 마법 어드벤처물로, ...  사실형  긍정  과거   확실   
16537  수족냉증은 어릴 때부터 심했으며 관절은 어디 한 곳이 아니고 목, 어깨, 팔꿈치, ...  사실형  긍정  과거   확실   
16538  김금희 소설가는 ＂계약서 조정이 그리 어려운가 작가를 격려한다면서 그런 문구 하나 ...  사실형  긍정  과거   확실   
16539  1만명이 넘는 방문자수를 기록한 이번 전시회는 총 77개 작품을 넥슨 사옥을 그대로...  사실형  긍정  과거  불확실   
16540                                      《목민심서》의 내용이다.  사실형  긍정  현재   확실   

               label  fold  
0       사실형-긍정-현재-확실     0  
1       사실형-긍정-과거-확실     3  
2       사실형-긍정-미래-확실     1  
3       사실형-긍정-과거-확실     2  
4       사실형-긍정-현재-확실     1  
...              ...   ...  
16536   사실형-긍정-과거-확실     2  
16537   사실형-긍정-과거-확실     0  
16538   사실형-긍정-과거-확실     1  
16539  사실형-긍정-과거-불확실     0  
16540   사실형-긍정-현재-확실     0  

[16541 rows x 9 columns]

In [125]:
data

유형  극성  시제 확실성
0      사실형  긍정  현재  확실
1      사실형  긍정  과거  확실
2      사실형  긍정  미래  확실
3      사실형  긍정  과거  확실
4      사실형  긍정  현재  확실
...    ...  ..  ..  ..
16536  사실형  긍정  과거  확실
16537  사실형  긍정  과거  확실
16538  사실형  긍정  과거  확실
16539  사실형  긍정  과거  확실
16540  사실형  긍정  현재  확실

[16541 rows x 4 columns]

In [123]:
data['pred1'].value_counts()

사실형    14099
추론형     1706
대화형      572
예측형      164
Name: pred1, dtype: int64

In [126]:
answer['유형'].value_counts()

사실형    13558
추론형     2151
대화형      575
예측형      257
Name: 유형, dtype: int64

In [156]:
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained('tunib/electra-ko-base')
num_added_toks = tokenizer.add_tokens(["[CLS1]", "[CLS2]", "[CLS3]", "[CLS4]", '＇'])


In [164]:
dict_ = {}
for i in tqdm(range(900)):
    tokens = tokenizer.tokenize(answer[(data['유형'] == '사실형') & (answer['유형'] == '추론형')].reset_index()['문장'][i])
    for token in tokens:
        if token not in dict_:
            dict_[token] = 1
        else:
            dict_[token] += 1

100%|███████████████████████████████████████████████████████████████████████████████| 900/900 [00:04<00:00, 192.75it/s]


In [165]:
dict_ = sorted(dict_.items(), key=lambda x: x[1], reverse=True)
dict_

[('.', 915),
 ('＇', 360),
 (',', 293),
 ('##을', 193),
 ('##의', 183),
 ('[UNK]', 175),
 ('##는', 166),
 ('있다', 161),
 ('수', 157),
 ('##에', 149),
 ('##다', 135),
 ('##이', 133),
 ('##가', 126),
 ('##도', 123),
 ('##은', 114),
 ('##를', 113),
 ('##한', 97),
 ('##과', 87),
 ('이', 85),
 ('##로', 78),
 ('##하는', 73),
 ('##할', 72),
 ('(', 72),
 (')', 72),
 ('##와', 62),
 ('##에서', 62),
 ('##했다', 62),
 ('·', 54),
 ('##으로', 53),
 ('##인', 50),
 ('등', 49),
 ('##고', 49),
 ('##하고', 49),
 ('있는', 46),
 ('##해', 46),
 ('고', 44),
 ('##까지', 37),
 ('##자', 36),
 ('##만', 36),
 ('##지', 35),
 ('것이다', 34),
 ('##사', 33),
 ('##이다', 32),
 ('한', 32),
 ('통해', 30),
 ('##서', 30),
 ('##나', 27),
 ('##기', 27),
 ('##적', 26),
 ('게임', 26),
 ('게', 26),
 ('것이', 24),
 ('한국', 23),
 ('더', 23),
 ('##적으로', 23),
 ('큰', 22),
 ('것으로', 22),
 ('대한', 22),
 ('특히', 22),
 ('##들이', 21),
 ('의', 21),
 ('##하게', 21),
 ('##된', 21),
 ('##대', 21),
 ('##한다', 21),
 ('전', 20),
 ('##야', 20),
 ('##하다', 20),
 ('##되는', 20),
 ('##었다', 20),
 ('영', 20),
 ('지난해', 20),
 